# **Proyecto 1 - Etapa I**

Integrantes:
* Santiago Rodriguez Bernal - 202011182
* Juan Camilo Pacheco Carvajal - 201913666


# 1. Entendimiento de los datos

In [3]:
#Instalaciones

#Y Data Profiling

!pip install ydata-profiling

#Libreria para remplazar numeros por palabras

!pip install num2words

#Deteccion de lenguaje para eliminar entradas que no esten en español

!pip install langdetect

#Procesamientno de lenguaje natural en español

!pip install stanza



In [7]:
!pip install --user stanza



  Using cached stanza-1.8.1-py3-none-any.whl.metadata (13 kB)
Using cached stanza-1.8.1-py3-none-any.whl (970 kB)


In [9]:
!pip install nltk

  Using cached click-8.1.7-py3-none-any.whl.metadata (3.0 kB)
   ---------------------------------------- 0.0/1.5 MB ? eta -:--:--
   ----------------------------- ---------- 1.1/1.5 MB 23.7 MB/s eta 0:00:01
   ---------------------------------------- 1.5/1.5 MB 23.8 MB/s eta 0:00:00
Using cached click-8.1.7-py3-none-any.whl (97 kB)


ERROR: Could not install packages due to an OSError: [WinError 2] The system cannot find the file specified: 'C:\\Python310\\Scripts\\nltk.exe' -> 'C:\\Python310\\Scripts\\nltk.exe.deleteme'



In [4]:

#Imports para procesamiento de texto

#Tokenizacion y lematizacion

import stanza

#Para integrar pasos de la limpieza adicionales

from stanza.pipeline.processor import Processor, register_processor

#Paquete español

stanza.download('es')

#Para manejo de numeros, singluares, plurarles en lenguaje

from num2words import num2words
#Deteccion de lenguaje

from langdetect import detect

from langdetect import DetectorFactory, detect_langs

# Librería Natural Language Toolkit, usada para trabajar con textos
import nltk

# Punkt permite separar un texto en frases.
nltk.download('stopwords')

from nltk.corpus import stopwords

#Operaciones con expresiones regulares y unicode
import re, string, unicodedata

2024-04-07 16:10:06 INFO: Downloaded file to C:\Users\zeify\stanza_resources\resources.json
2024-04-07 16:10:06 INFO: Downloading default packages for language: es (Spanish) ...
2024-04-07 16:10:08 INFO: File exists: C:\Users\zeify\stanza_resources\es\default.zip
2024-04-07 16:10:13 INFO: Finished downloading models and saved to C:\Users\zeify\stanza_resources
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\zeify\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [5]:
#Imports generales para analisis de datos y ML
import pandas as pd
import numpy as np
import sys
import statistics
from ydata_profiling import ProfileReport

import sklearn
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer

from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, classification_report

from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import RandomForestClassifier

In [6]:
# Lectura de los datos.
df_turi = pd.read_csv('tipo2_entrenamiento_estudiantes.csv', sep=',', encoding='utf-8')

df_turi.head()

Review  Class
0  Muy buena atención y aclaración de dudas por p...      5
1  Buen hotel si están obligados a estar cerca de...      3
2  Es un lugar muy lindo para fotografías, visite...      5
3  Abusados con la factura de alimentos siempre s...      3
4  Tuvimos un par de personas en el grupo que rea...      3

In [7]:
df_turi.dtypes

Review    object
Class      int64
dtype: object

# Impresion Reporte Y Data Profiling

In [8]:
!pip install --user ipywidgets

In [13]:
reviews = df_turi.copy()
#Longitud del comentario (numero de caracteres)
reviews['Conteo'] = [len(x) for x in reviews['Review']]
#Palabra(s) mas frecuente(s)
reviews['Moda'] = [max(set(x.split(' ')), key = x.split(' ').count) for x in reviews['Review']]
#Longitud de la palabra mas larga del comentario
reviews['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in reviews['Review']]
#Longitud de la palabra mas corta del comentario
reviews['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in reviews['Review']]

profile = ProfileReport(reviews, title='Profiling Report', explorative=True)

profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
#Conteo de entradas nulas
df_turi.isnull().sum()

Review    0
Class     0
dtype: int64

In [17]:
from langdetect import DetectorFactory
#Verificamos entradas en otros idiomas
DetectorFactory.seed = 42
x =df_turi[df_turi.Review.map(detect)  != 'es']

x.to_csv('output.csv', index=False)

x


Review  Class
296   Excelente! Servicio estuvo excelente. \nLa com...      5
711   mas o menos estan mejor las de saltillo lñdkjv...      2
3749  First part of the tour was Rivera's actual hom...      2
4490                                          esta rico      4
6518  A few months after ciudad perdida we keep on t...      5
6869  Cementerio Antiguo. Patrimonio Mundial. facil ...      5
7455  This university is unique around the world. Th...      5

Una observacion es que la libreria no esta funcionando correctamente en su totalidad pues tenemos 3 entradas escritas en español, que fueron detectadas erroneamente como en otro idioma por lo que al hacer la eliminacion las tendremos encuenta

In [15]:
#Revisamos los registros duplicados
df_turi.duplicated().sum()


duplicated_rows = df_turi[df_turi.duplicated()]
print(duplicated_rows)




                                                 Review  Class
579   El lugar es una maravilla que merece ser visit...      2
1067  El lugar es una maravilla que merece ser visit...      2
1637  El lugar es una maravilla que merece ser visit...      2
1811  El lugar es una maravilla que merece ser visit...      2
1870  El lugar es una maravilla que merece ser visit...      2
...                                                 ...    ...
7194  Deben de actualizar los horarios en las difere...      3
7217  Que lastima de lugar, es muy bonito visualment...      2
7325  Excelente lugar, bien conservado, limpio, adec...      5
7357  La ciudad es bonita, pero la gente deja muchis...      1
7524  Deben de actualizar los horarios en las difere...      3

[73 rows x 2 columns]


# 2. Preparacion de los datos

In [18]:
#Eliminamos entradas en otros idiomas
df_turi = df_turi.drop(x.index)

In [19]:
#Eliminamos entradas duplicadas
df_turi = df_turi.drop_duplicates()

In [20]:
#Verificamos cuantos datos quedan
df_turi.shape

(7795, 2)

## 2.1 Limpieza, tokenizacion y lemmatizacion

In [52]:
#Remplaza los numeros por su representacion en palabras
def replace_numbers(words):
    """Replace all interger occurrences in list of tokenized words with textual representation"""
    new_words = []
    for word in words:
        if word.isdigit():
            new_word = num2words(word, lang='es')
            new_words.append(new_word)
        else:
            new_words.append(word)
    return new_words
#Remueve todo caracter no latino (conserva espacios y numeros)
def remove_nonlatin(words):
  new_words = []
  for word in words:
    new_word = ''
    for ch in word:
      if unicodedata.name(ch).startswith(('LATIN', 'DIGIT', 'SPACE')):
        new_word += ch
    new_words.append(new_word)
  return new_words

#Remueve palabras comunes que no aportan informacion
def remove_stopwords(words):
    """Remove stop words from list of tokenized words"""
    new_words = []
    s = set(stopwords.words('spanish'))
    for word in words:
        if word not in s:
            new_words.append(word)
    return new_words

#Remueve puntuacion
def remove_punctuation(words):
    """Remove punctuation from list of tokenized words"""
    new_words = ''
    for word in words:
            new_words += re.sub(r'[^\w\s]', ' ', word)
    return new_words

 #Procesamiento de cada review usando stanza
def tokenLemma():
  df_turi['words'] = df_turi['Review'].apply(remove_punctuation)
  #Creamos un pipeline para tokenizacion y lematizacion
  nlp = stanza.Pipeline('es', processors = 'tokenize,mwt,pos,lemma', use_gpu=True)
  in_docs = [stanza.Document([], text=d) for d in df_turi.words]
  return nlp(in_docs)

#Funcion secundaria para procesar cada token
def procesamientoPalabras(words):
    words = remove_nonlatin(words)
    words = replace_numbers(words)
    words = remove_stopwords(words)
    return words

#Funcion principal para el pre-procesamiento
def preprocessing():
  out_docs = tokenLemma()
  palabras = []

  for doc in out_docs:
    reviewAct = []
    for sentence in doc.sentences:
      for word in sentence.words:
        if(word.pos != 'PUNCT' and word.pos != 'SYM'):
          reviewAct.append(word.lemma.lower())
    palabras.append(reviewAct)

  df_turi['words'] = palabras
  df_turi['words'] = df_turi['words'].apply(procesamientoPalabras)

In [22]:
# LLamamos la funcion
#Descomentar el processing si se quiere revisar, si no el resultado con los datos procesados esta en el archivo df_procesado
#No descomentar se demoro 80 minutos xD
#preprocessing()

In [23]:

#Guardamos los datos procesados. Descomentar si se quiere crear el archivo despues de procesar los datos.
#df_turi.to_csv('df_procesado.csv', index=False, sep= ",")

#Leemos los datos procesados
df_turi_Pre = pd.read_csv("df_procesado.csv", sep = ",", encoding='utf-8')
import ast
df_turi_Pre['words'] = df_turi_Pre['words'].apply(ast.literal_eval)

In [24]:
#Visualizar los cambios
df_turi_Pre.head()

Review  Class  \
0  Muy buena atención y aclaración de dudas por p...      5   
1  Buen hotel si están obligados a estar cerca de...      3   
2  Es un lugar muy lindo para fotografías, visite...      5   
3  Abusados con la factura de alimentos siempre s...      3   
4  Tuvimos un par de personas en el grupo que rea...      3   

                                               words  
0  [buen, atención, aclaración, duda, parte, seño...  
1  [buen, hotel, si, obligado, cerca, centro, con...  
2  [ser, lugar, lindo, fotografía, visitar, selin...  
3  [abusado, factura, alimento, siempre, echar, c...  
4  [tener, par, persona, grupo, realmente, querer...

In [25]:
#Convertimos los tokens nuevamente en strings
df_turi_Pre['words'] = df_turi_Pre['words'].apply(lambda x: ' '.join(map(str, x)))
df_turi_Pre

Review  Class  \
0     Muy buena atención y aclaración de dudas por p...      5   
1     Buen hotel si están obligados a estar cerca de...      3   
2     Es un lugar muy lindo para fotografías, visite...      5   
3     Abusados con la factura de alimentos siempre s...      3   
4     Tuvimos un par de personas en el grupo que rea...      3   
...                                                 ...    ...   
7863  Me parece buen sistema, agiliza el transporte,...      4   
7864  Fue una escapada de un día desde el complejo, ...      4   
7865  La Plaza de la Revolución es un lugar emblemát...      3   
7866  Es la segunda ocasión que me quedo en los cuar...      1   
7867  Llegamos por casualidad a Los Mercaderes, un g...      5   

                                                  words  
0     buen atención aclaración duda parte señorita v...  
1     buen hotel si obligado cerca centro convención...  
2     ser lugar lindo fotografía visitar selina músi...  
3     abusado factura alimento siempre echar culpa i...  
4     tener par persona grupo realmente querer comer...  
...                                                 ...  
7863  parecer buen sistema agilizar transporte conec...  
7864  ser escapada día complejo ir grupo turista hab...  
7865  plaza revolución ser lugar emblemático identif...  
7866  ser segundo ocasión quedar cuarto area jardín ...  
7867  llegar casualidad mercaderes grupo grande vari...  

[7868 rows x 3 columns]

### 2.1.1 Verificamos los datos obtenidos

In [26]:
reseñas = df_turi_Pre.copy()
#Longitud del comentario (numero de caracteres)
reseñas['Conteo'] = [len(x) for x in reseñas['words']]
#Palabra(s) mas frecuente(s)
reseñas['Moda'] = [max(set(x.split(' ')), key = x.split(' ').count) for x in reseñas['words']]
#Longitud de la palabra mas larga del comentario
reseñas['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in reseñas['words']]
#Longitu de la palabra mas corta del comentario
reseñas['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in reseñas['words']]

profile2 = ProfileReport(reseñas, title='Profiling Report', explorative=True)

profile2

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## 2.2 Separacion de los datos y vectorización

In [27]:
#Separación de los datos en conjunto de test y train
df_turi_Pre = df_turi_Pre.drop('Review', axis = 1)
df_train, df_test = sklearn.model_selection.train_test_split(df_turi_Pre, test_size=0.2, random_state=0)

X_train = df_train['words']
y_train = df_train['Class']

X_test = df_test['words']
y_test = df_test['Class']

In [28]:
#Vectorizar los datos con Tfid
vectorizer = TfidfVectorizer()
train_vectors = vectorizer.fit_transform(X_train)
test_vectors = vectorizer.transform(X_test)
print(train_vectors.shape, test_vectors.shape)

(6294, 14683) (1574, 14683)


# 3. Modelado y evaluacion

## 3.1 Logistic Regression - Juan Camilo Pacheco

In [29]:
from matplotlib import style
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LogisticRegression
import sklearn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import SVC
from sklearn import metrics
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, classification_report

In [30]:

from sklearn.model_selection import GridSearchCV

# parameter grid para evaluar el mejor modelo
parameters = {
    'penalty' : ['l1','l2', 'elasticnet', None], 
    'C'       : np.logspace(-10,10,3),
    'solver'  : ['newton-cg', 'lbfgs', 'liblinear'],
}
     

In [31]:
#Implementar la regresin con k-fold cross validation
from sklearn.model_selection import RepeatedKFold
metrica = RepeatedKFold(n_splits=20, n_repeats= 10, random_state=0)

logreg = LogisticRegression()
modelo = GridSearchCV(logreg, param_grid = parameters, scoring='accuracy', cv=metrica, n_jobs=-1)  

In [32]:
modelo.fit(train_vectors,y_train)
print("Tuned Hyperparameters :", modelo.best_params_)
print("Accuracy :",modelo.best_score_)
modelo_optimo = modelo.best_estimator_

d:\AnacondaNavigator\Lib\site-packages\sklearn\model_selection\_validation.py:378: FitFailedWarning: 
3600 fits failed out of a total of 7200.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
600 fits failed with the following error:
Traceback (most recent call last):
  File "d:\AnacondaNavigator\Lib\site-packages\sklearn\model_selection\_validation.py", line 686, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "d:\AnacondaNavigator\Lib\site-packages\sklearn\linear_model\_logistic.py", line 1162, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "d:\AnacondaNavigator\Lib\site-packages\sklearn\linear_model\_logistic.py",

Tuned Hyperparameters : {'C': 1.0, 'penalty': 'l2', 'solver': 'newton-cg'}
Accuracy : 0.48655803255484786


In [33]:
#Medimos exatitud sobre el test
prediccion = modelo_optimo.predict(test_vectors)
score = modelo_optimo.score(test_vectors, y_test)

print("Exactitud predicción test: " + str(score))

Exactitud predicción test: 0.49682337992376113


In [34]:
#Encontramos la matriz de confusion con los resultados
matriz_confusion = metrics.confusion_matrix(y_test, prediccion)
print(matriz_confusion)

[[ 55  54  20   8   9]
 [ 28  80  74  28  28]
 [ 11  57 130  86  41]
 [  3  13  54 171 160]
 [  0   2  24  92 346]]


In [35]:
# Reporte de metricas
reporte = classification_report(y_test, prediccion)
print(reporte)

              precision    recall  f1-score   support

           1       0.57      0.38      0.45       146
           2       0.39      0.34      0.36       238
           3       0.43      0.40      0.41       325
           4       0.44      0.43      0.44       401
           5       0.59      0.75      0.66       464

    accuracy                           0.50      1574
   macro avg       0.48      0.46      0.46      1574
weighted avg       0.49      0.50      0.49      1574



## 3.2 MultinomialNB - Santiago Rodriguez Bernal

In [36]:
from sklearn.naive_bayes import MultinomialNB
multinomial = MultinomialNB().fit(train_vectors, y_train)

y_pred = multinomial.predict(test_vectors)

print("Score: ", multinomial.score(train_vectors, y_train))
print('Accuracy:', accuracy_score(y_test, y_pred))
print('F1 score:', f1_score(y_test, y_pred, average="macro"))

Score:  0.6220209723546235
Accuracy: 0.39072426937738247
F1 score: 0.2610357125807726


In [37]:
confusion_matrix(y_test, y_pred)

array([[  0,  42,  47,  24,  33],
       [  0,  27,  73,  74,  64],
       [  0,  18,  62, 139, 106],
       [  0,   2,  14, 121, 264],
       [  0,   0,   1,  58, 405]], dtype=int64)

In [38]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           1       0.00      0.00      0.00       146
           2       0.30      0.11      0.17       238
           3       0.31      0.19      0.24       325
           4       0.29      0.30      0.30       401
           5       0.46      0.87      0.61       464

    accuracy                           0.39      1574
   macro avg       0.27      0.30      0.26      1574
weighted avg       0.32      0.39      0.33      1574



d:\AnacondaNavigator\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
d:\AnacondaNavigator\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
d:\AnacondaNavigator\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


## 3.3 Random Forest - Santiago Rodriguez - Juan Camilo Pacheco


In [39]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

clasif = RandomForestClassifier(random_state=0)
clasif.fit(train_vectors, y_train)
ytest_pred = clasif.predict(test_vectors)

clasif = RandomForestClassifier(random_state=0)
clasif.fit(train_vectors, y_train)
predicted = clasif.predict(test_vectors)
class_report = classification_report(y_test, predicted)
print("\nClassification Report")
print(class_report)


Classification Report
              precision    recall  f1-score   support

           1       0.50      0.17      0.26       146
           2       0.36      0.35      0.36       238
           3       0.38      0.27      0.32       325
           4       0.41      0.32      0.36       401
           5       0.49      0.79      0.60       464

    accuracy                           0.44      1574
   macro avg       0.43      0.38      0.38      1574
weighted avg       0.43      0.44      0.41      1574



In [41]:
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier

#Se fijan 5 particiones teniendo en cuenta los datos que estamos manejando.
particiones = KFold(n_splits=5, shuffle=True, random_state = 0)

# Establecemos el espacio de búsqueda para los hiperparámetros en especial los que nos permiten controlar la complejidad y el rendimiento del modelo
param_grid = {'criterion':['gini', 'entropy'],'min_samples_split':[2, 4, 6],'max_features':[10, 100, 1000]}

forest = RandomForestClassifier(random_state=0)
modelo = GridSearchCV(forest, param_grid, cv=particiones, refit = True, scoring = 'accuracy')
modelo.fit(train_vectors, y_train)

print(modelo.best_params_)  #MMejor modelo escogido

clasif = modelo.best_estimator_
predicted = clasif.predict(test_vectors)
class_report = classification_report(y_test, predicted)
print("\nClassification Report")
print(class_report)

{'criterion': 'gini', 'max_features': 1000, 'min_samples_split': 6}

Classification Report
              precision    recall  f1-score   support

           1       0.55      0.28      0.37       146
           2       0.41      0.40      0.40       238
           3       0.41      0.32      0.36       325
           4       0.39      0.35      0.37       401
           5       0.52      0.73      0.61       464

    accuracy                           0.46      1574
   macro avg       0.45      0.42      0.42      1574
weighted avg       0.45      0.46      0.44      1574



In [42]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test, predicted)

0.4567979669631512

In [43]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test, predicted)

0.4567979669631512

# 4. Predicción

## 4.1 Lectura y preparación de los datos

In [53]:
df_turi = pd.read_csv('particion_prueba_estudiantes.csv', encoding='utf-8')

df_turi.head()

Review
0  La primera noche nos encontramos en la habitac...
1  A una calle de catedral con platillos tradicio...
2  Porciones muy miserables\nAgua con sabor a clo...
3  Cartagena encanta. De todas las ciudades colon...
4  Ibamos con mucha ilusion de disfrutar el espec...

In [54]:
preprocessing()

2024-04-07 19:59:39 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2024-04-07 19:59:39 INFO: Downloaded file to C:\Users\zeify\stanza_resources\resources.json
2024-04-07 19:59:39 INFO: Loading these models for language: es (Spanish):
| Processor | Package         |
-------------------------------
| tokenize  | ancora          |
| mwt       | ancora          |
| pos       | ancora_charlm   |
| lemma     | ancora_nocharlm |

2024-04-07 19:59:39 WARNING: GPU requested, but is not available!
2024-04-07 19:59:39 INFO: Using device: cpu
2024-04-07 19:59:39 INFO: Loading: tokenize
2024-04-07 19:59:39 INFO: Loading: mwt
2024-04-07 19:59:39 INFO: Loading: pos
2024-04-07 19:59:40 INFO: Loading: lemma
2024-04-07 19:59:40 INFO: Done loading processors!


In [57]:
# Cargamos los datos procesados
df_turi.to_csv('df_procesado_predecir.csv', index=False, sep= ";")
#Leemos los datos procesados
df_turi_Predict = pd.read_csv("df_procesado_predecir.csv", sep = ";", encoding='utf-8')
import ast
df_turi_Predict['words'] = df_turi_Predict['words'].apply(ast.literal_eval)



In [58]:
df_turi_Predict.head()

Review  \
0  La primera noche nos encontramos en la habitac...   
1  A una calle de catedral con platillos tradicio...   
2  Porciones muy miserables\nAgua con sabor a clo...   
3  Cartagena encanta. De todas las ciudades colon...   
4  Ibamos con mucha ilusion de disfrutar el espec...   

                                               words  
0  [primero, noche, encontrar, habitación, nido, ...  
1  [calle, catedral, platillo, tradicional, tipo,...  
2  [porción, miserable, agua, sabor, cloro, distr...  
3  [cartagena, encantar, ciudad, colonial, haber,...  
4  [ir, ilusion, disfrutar, espectaculo, luz, son...

In [59]:
#Convertimos los tokens nuevamente en strings
df_turi_Predict['words'] = df_turi_Predict['words'].apply(lambda x: ' '.join(map(str, x)))
df_turi_Predict

Review  \
0     La primera noche nos encontramos en la habitac...   
1     A una calle de catedral con platillos tradicio...   
2     Porciones muy miserables\nAgua con sabor a clo...   
3     Cartagena encanta. De todas las ciudades colon...   
4     Ibamos con mucha ilusion de disfrutar el espec...   
...                                                 ...   
1745  Subir en funicular y bajar en teleferico fue u...   
1746  La gente espera el lugar central en La Habana,...   
1747  Todo excelente con el hotel: las albercas para...   
1748  Nos detuvimos en un bocado antes de la puesta ...   
1749  NO TENIA AGUA, el mantenimiento un desastre ( ...   

                                                  words  
0     primero noche encontrar habitación nido cinco ...  
1     calle catedral platillo tradicional tipo gourm...  
2     porción miserable agua sabor cloro distraído m...  
3     cartagena encantar ciudad colonial haber visit...  
4     ir ilusion disfrutar espectaculo luz sonido ve...  
...                                                 ...  
1745  subir funicular bajar teleferico ser buen expe...  
1746  gente esperar lugar central habana fiesta naci...  
1747  excelente hotel alberca niño mejor atención me...  
1748  detener bocado puesta sol haber nadie restaura...  
1749  tener agua mantenimiento desastre mochila baño...  

[1750 rows x 2 columns]

In [60]:
#Separar datos para predecir
df_turi_Predict = df_turi_Predict.drop('Review', axis = 1)

X_predict = df_turi_Predict['words']

In [61]:
X_predict

0       primero noche encontrar habitación nido cinco ...
1       calle catedral platillo tradicional tipo gourm...
2       porción miserable agua sabor cloro distraído m...
3       cartagena encantar ciudad colonial haber visit...
4       ir ilusion disfrutar espectaculo luz sonido ve...
                              ...                        
1745    subir funicular bajar teleferico ser buen expe...
1746    gente esperar lugar central habana fiesta naci...
1747    excelente hotel alberca niño mejor atención me...
1748    detener bocado puesta sol haber nadie restaura...
1749    tener agua mantenimiento desastre mochila baño...
Name: words, Length: 1750, dtype: object

In [62]:
#Vectorizar los datos con Tfid
vectors = vectorizer.transform(X_predict)
print(vectors.shape)

(1750, 14683)


In [63]:
#Predecir los datos y guardarlos en el archivo

predict = modelo_optimo.predict(vectors)

df_turi_Predict["Review"] = df_turi["Review"]
df_turi_Predict["Class"] = predict

df_turi_Predict = df_turi_Predict[["Review", "Class"]]
df_turi_Predict.to_csv('Resultado_predicciones.csv', index=False)

df_turi_Predict.head()

Review  Class
0  La primera noche nos encontramos en la habitac...      1
1  A una calle de catedral con platillos tradicio...      5
2  Porciones muy miserables\nAgua con sabor a clo...      2
3  Cartagena encanta. De todas las ciudades colon...      5
4  Ibamos con mucha ilusion de disfrutar el espec...      4

In [68]:
prediccion = modelo_optimo.predict(vectors)
score = modelo_optimo.score(vectors, predict)

print("Exactitud predicción test: " + str(score))

Exactitud predicción test: 1.0
